In [ ]:
!pip install nltk

In [ ]:
import nltk
nltk.download()

NLTK Downloader
---------------------------------------------------------------------------
    d) Download   l) List    u) Update   c) Config   h) Help   q) Quit
---------------------------------------------------------------------------
Downloader> q


True

In [ ]:
pip install openai

In [ ]:
import json
from string import punctuation
import os
import re
import datetime
import math

In [ ]:
from google.colab import drive
drive.mount('/content/drive')
checkpoints = '/content/drive/MyDrive/colab_files/'
if not os.path.exists(checkpoints):
    os.makedirs(checkpoints)

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [ ]:
def nv_preprocess(nv_json_path, trim=None):    
    """
    Loads JSON into environment as dictionary
    Preprocesses the raw PDF export from previously generated json    
    Optional: Trims transcript to exclude list of those present and signature page/list of exhibits
    
    Parameters
    ----------
    nv_json_path : STRING
        Local path of nv_json generated by nv_pdftotext.
    trim: TRUE/Default(NONE)
        Provides option to trim transcript to spoken section and transcriber notes
        
    Returns
    -------
    Cleaned dictionary that excludes PDF formatting and (optional) front and back end 

    """
    
    file_path = open(nv_json_path,'rb')
    data = json.load(file_path)
    
    if trim:
        for key in data:
            if isinstance(data[key], str):
                ##Removes list of attendees on front end
                start_location = re.search(r"(CHAIR.*[A-z]\:|Chair.*[A-z]\:)", data[key]).start() #Chair speaks first
                data[key] = data[key][start_location:] #Starts transcript from when Chair first speaks
                ##Removes signature page after submission (RESPECTFULLY SUBMITTED)
                end_location = re.search(r"(Respectfully\sSUBMITTED\:|RESPECTFULLY\sSUBMITTED\:)", data[key]).start() #Signature page starts with
                data[key] = data[key][:end_location] #End transcript just before respectfully submitted            
                ##PDF formatting
                data[key] = re.sub(r"Page\s[0-9]{1,}", "", data[key]) #Removes page number
                data[key] = re.sub(r"\n", "", data[key])
                data[key] = data[key].strip()
                data[key]=" ".join(data[key].split())
            elif isinstance(data[key], list):
                for i in range(len(data[key])):
                    start_location = re.search(r"(CHAIR.*[A-z]\:|Chair.*[A-z]\:)", data[key][i]).start() #Chair speaks first
                    data[key][i] = data[key][i][start_location:] #Starts transcript from when Chair first speaks
                    end_location = re.search(r"(Respectfully\sSUBMITTED\:|RESPECTFULLY\sSUBMITTED\:|RESPECTFULLY\sSUBMITTED)",
                                             data[key][i]).start()  # Signature page starts with
                    ##Removes signature page after submission (RESPECTFULLY SUBMITTED)
                    # try:
                    #     end_location = re.search(r"(Respectfully\sSUBMITTED\:|RESPECTFULLY\sSUBMITTED\:)", data[key][i]).start() #Signature page starts with
                    # except:
                    #     end_location = -1
                    data[key][i] = data[key][i][:end_location] #End transcript just before respectfully submitted
                    ##PDF formatting
                    data[key][i] = re.sub(r"Page\s[0-9]{1,}", "", data[key][i]) #Removes page number
                    data[key][i] = re.sub(r"\n", "", data[key][i])
                    data[key][i] = data[key][i].strip()
                    data[key][i]=" ".join(data[key][i].split())
            else:
                print("Incompatible File")

        return(data)
            
    else:
        for key in data:
            if isinstance(data[key], str):          
                ##PDF formatting
                data[key] = re.sub(r"Page\s[0-9]{1,}", "", data[key]) #Removes page number
                data[key] = re.sub(r"\n", "", data[key])
                data[key] = data[key].strip()
                data[key]=" ".join(data[key].split())
            elif isinstance(data[key], list):
                for i in range(len(data[key])):      
                    ##PDF formatting
                    data[key][i] = re.sub(r"Page\s[0-9]{1,}", "", data[key][i]) #Removes page number
                    data[key][i] = re.sub(r"\n", "", data[key][i])
                    data[key][i] = data[key][i].strip()
                    data[key][i]=" ".join(data[key][i].split())
            else:
                print("Incompatible File")

        return(data)

In [ ]:
file_name = "nv_hhs_m_2021.json"
data = nv_preprocess(checkpoints + file_name, trim=True)

In [ ]:
def json_split_by_date(json_file):
    """
    
    Parameters
    ----------
    Local path of nv_json generated by nv_pdftotext.
        Local path of cleaned nv_json file. 
    Returns
    -------
    A new json file with month as the keys. We can call new_json_file[month] if we want the transcripts of meetings for this month.
    Eg: call new_json_file[4], we would get the transcripts for April.

    """
    json_date = {}
    month = ['January', 'February', 'March', 'April', 'May', 'June', 'July', 'August', 'September', 'October', 'November', 'December']

    for key in json_file.keys():
      for doc in json_file[key]:
        rx = r'{0}[ ]([1-9]|[12][0-9]|3[01])[,][ ](2020|2021)'.format(month[int(key)-1])
        match = re.search(rx, doc)
        date = datetime.datetime.strptime(match.group(), '%B %d, %Y').date()
        json_date[date] = doc
    return json_date

In [ ]:
data = json_split_by_date(data)

In [ ]:
list_sen=[]
k = 0
for i in data.keys():
  temp=nltk.tokenize.sent_tokenize(data[i])
  for j in range(len(temp)):
    list_sen.append({'text':temp[j], 'metadata': i.strftime("%m/%d/%Y")+"-"+str(j)})
    k += 1

In [ ]:
pip install -U sentence-transformers

     |████████████████████████████████| 78 kB 3.4 MB/s 
     |████████████████████████████████| 3.1 MB 11.6 MB/s 
     |████████████████████████████████| 3.3 MB 33.6 MB/s 
     |████████████████████████████████| 1.2 MB 24.4 MB/s 
     |████████████████████████████████| 59 kB 6.6 MB/s 
     |████████████████████████████████| 596 kB 44.5 MB/s 
     |████████████████████████████████| 895 kB 48.4 MB/s 
  Created wheel for sentence-transformers: filename=sentence_transformers-2.1.0-py3-none-any.whl size=121000 sha256=423dcfbfd4dde544085276e5168e5195e1336f1be6ebabc09c64aaa3fbc67ff4
  Stored in directory: /root/.cache/pip/wheels/90/f0/bb/ed1add84da70092ea526466eadc2bfb197c4bcb8d4fa5f7bad
Successfully built sentence-transformers
  Attempting uninstall: pyyaml
    Found existing installation: PyYAML 3.13
    Uninstalling PyYAML-3.13:
      Successfully uninstalled PyYAML-3.13


In [ ]:
from sentence_transformers import SentenceTransformer, util
import torch

In [ ]:
corpus = [text['text'] for text in list_sen]

In [ ]:
embedder = SentenceTransformer('all-MiniLM-L6-v2')

# Corpus with example sentences
corpus_embeddings = embedder.encode(corpus, convert_to_tensor=True)


In [ ]:
query = 'COVID 19'
top_k = len(corpus)//20

In [ ]:
results = set()

In [ ]:
query_embedding = embedder.encode(query, convert_to_tensor=True)

# We use cosine-similarity and torch.topk to find the highest 5 scores
cos_scores = util.pytorch_cos_sim(query_embedding, corpus_embeddings)[0]
top_results = torch.topk(cos_scores, k=top_k)

print("\n\n======================\n\n")
print("Query:", query)
print("\nTop " + str(top_k) + " most similar sentences in corpus:")

for score, idx in zip(top_results[0], top_results[1]):
    if len(corpus[idx]) > 10:
      results.add(corpus[idx])
      print(corpus[idx], "(Score: {:.4f})".format(score))





Query: COVID 19

Top 1218 most similar sentences in corpus:
We are doing research, but I have not heard anything specific to Covid-19. (Score: 0.7449)
We are still wrestling with what effects COVID-19 has had. (Score: 0.6983)
We are currently living in unprecedented times with COVID-19. (Score: 0.6779)
Here is a quick overview of our COVID-19 response [page 57]. (Score: 0.6778)
Today, the focus is COVID-19; however, in the future, it could be something else—a disaster of some sort, another pandemic, or a statewide emergency. (Score: 0.6713)
We plan to reactivate those, post-COVID-19. (Score: 0.6644)
As a disaster, COVID-19 has impacted virtually everyone in one way or another. (Score: 0.6568)
That has been expanded significantly by the COVID-19 response. (Score: 0.6524)
We have been fighting COVID-19 as everyone else has in the last year. (Score: 0.6481)
Covid-19 took my father’s life a few months ago. (Score: 0.6461)
Those things were exacerbated by Covid-19. (Score: 0.6391)
What 

In [ ]:
filter = {}
for i in data.keys():
  temp=nltk.tokenize.sent_tokenize(data[i])
  filter[i] = []
  for j in range(len(temp)):
    if temp[j] in results:
      filter[i].append(temp[j])
    else:
      pass

In [ ]:
filter

{datetime.date(2021, 2, 3): ['This is a virtual meeting format and meant to keep us safe during the COVID-19 pandemic, but I also see it as an opportunity for members of the public to provide testimony in a variety of different ways which they may not have been able to utilize in the past.',
  'Hopefully, as we eventually move to a situation where we are meeting in person and taking testimony in person, we will still allow some of the public to participate in the new ways we have developed around the COVID-19 protocol.',
  'Assemblyman Hafen: I represent District 36, and this is my second session on the Health and Human Services Committee.',
  'The pandemic caused by the coronavirus disease of 2019, COVID-19, will dominate any measures you will consider this session either directly or indirectly.',
  "Richard Whitley, Director, Department of Health and Human Services: I am grateful that the Chair has allowed us to take some deeper dives into aspects of health and human services such as

In [ ]:
import spacy

In [ ]:
# run this from a normal command line
!python -m spacy download en
!python -m spacy download en_core_web_md

     |████████████████████████████████| 12.0 MB 5.3 MB/s 
✔ Download and installation successful
You can now load the model via spacy.load('en_core_web_sm')
✔ Linking successful
/usr/local/lib/python3.7/dist-packages/en_core_web_sm -->
/usr/local/lib/python3.7/dist-packages/spacy/data/en
You can now load the model via spacy.load('en')
     |████████████████████████████████| 96.4 MB 41.0 MB/s 
✔ Download and installation successful
You can now load the model via spacy.load('en_core_web_md')


In [ ]:
!python -m spacy download en_core_web_lg
!python -m spacy download en_core_web_sm

     |████████████████████████████████| 827.9 MB 1.0 MB/s 
  Created wheel for en-core-web-lg: filename=en_core_web_lg-2.2.5-py3-none-any.whl size=829180942 sha256=e6294f3ad7bc9747c62e90a8a7c868c3961e9a5a07d3aa17f474c1ad6d3c9484
  Stored in directory: /tmp/pip-ephem-wheel-cache-jjw7wweh/wheels/11/95/ba/2c36cc368c0bd339b44a791c2c1881a1fb714b78c29a4cb8f5
Successfully built en-core-web-lg
✔ Download and installation successful
You can now load the model via spacy.load('en_core_web_lg')
     |████████████████████████████████| 12.0 MB 5.3 MB/s 
✔ Download and installation successful
You can now load the model via spacy.load('en_core_web_sm')


In [ ]:
# Load the spacy model that you have installed
nlp = spacy.load('en')
nlp = spacy.load('en_core_web_sm')
query = nlp('COVID 19')
q_similarity = []
for sentence in corpus:
  # process a sentence using the model
  doc = nlp(sentence)
  q_similarity.append(doc.similarity(query))

流式输出内容被截断，只能显示最后 5000 行内容。
/usr/lib/python3.7/runpy.py:193: ModelsWarning: [W007] The model you're using has no word vectors loaded, so the result of the Doc.similarity method will be based on the tagger, parser and NER, which may not give useful similarity judgements. This may happen if you're using one of the small models, e.g. `en_core_web_sm`, which don't ship with word vectors and only use context-sensitive tensors. You can always add your own word vectors, or use one of the larger models instead if available.
  "__main__", mod_spec)
/usr/lib/python3.7/runpy.py:193: ModelsWarning: [W007] The model you're using has no word vectors loaded, so the result of the Doc.similarity method will be based on the tagger, parser and NER, which may not give useful similarity judgements. This may happen if you're using one of the small models, e.g. `en_core_web_sm`, which don't ship with word vectors and only use context-sensitive tensors. You can always add your own word vectors, or use one of t

In [ ]:
import numpy as np
q_similarity_argsort = np.argsort(q_similarity)

In [ ]:
corpus[np.argmax(q_similarity)]

'ASSEMBLYWOMAN GORELOW MADE A MOTION TO INTRODUCE BDR 38-449.'

In [ ]:
spa_results = set()
for i in range(len(corpus)-1, len(corpus) - len(corpus)//20, -1):
  spa_results.add(corpus[q_similarity_argsort[i]])
  print(corpus[q_similarity_argsort[i]])

ASSEMBLYWOMAN GORELOW MADE A MOTION TO INTRODUCE BDR 38-449.
ASSEMBLYWOMAN TITUS MADE A MOTION TO INTRODUCE BDR 38-385 AND BDR 40-454.
ASSEMBLYWOMAN GORELOW MADE A MOTION TO INTRODUCE BDR 38-452.
(BDR 40-478) SENATOR HEIDI SEEVERS GANSERT (Senatorial District No.
SENATOR HARRIS MOVED TO RESCIND THE PREVIOUS ACTION TAKEN ON BDR 40-1107.
Assembly Joint Resolution 1 was heard on February 10, 2021.
ASSEMBLYWOMAN THOMAS MADE A MOTION TO DO PASS SENATE BILL 61 (1ST REPRINT).
(BDR 54-61) ASSEMBLYWOMAN TERESA BENITEZ-THOMPSON (Assembly District No.
SENATOR SPEARMAN MOVED TO INTRODUCE BDR 40-1107.
(BDR 40-96) ASSEMBLYWOMAN LESLEY E. COHEN (ASSEMBLY DISTRICT NO.
(BDR 40-998) SENATOR ROBERTA LANGE (Senatorial District No.
ASSEMBLYWOMAN TITUS MADE A MOTION TO DO PASS ASSEMBLY BILL 16.
(BDR 40-8) SENATOR DINA NEAL (Senatorial District No.
ASSEMBLYWOMAN TITUS MADE A MOTION TO DO PASS ASSEMBLY BILL 26.
Assembly Committee on Health and Human Services March 3, 2021 ASSEMBLYWOMAN THOMAS MADE A MOTION TO

In [ ]:
for i in data.keys():
  i.strftime("%m/%d/%Y")
  print(i)

2021-04-28
2021-04-02
2021-04-05
2021-04-09
2021-04-21
2021-04-23
2021-04-27
2021-04-29
2021-04-01
2021-04-06
2021-04-08
2021-04-13
2021-04-22
2021-05-03
2021-05-05
2021-05-07
2021-05-24
2021-05-27
2021-05-04
2021-05-06
2021-05-11
2021-05-13
2021-05-18
2021-05-25
2021-02-03
2021-02-08
2021-02-10
2021-02-15
2021-02-17
2021-02-22
2021-02-24
2021-02-16
2021-02-18
2021-02-04
2021-02-09
2021-02-11
2021-03-03
2021-03-08
2021-03-10
2021-03-15
2021-03-19
2021-03-22
2021-03-24
2021-03-26
2021-03-29
2021-03-31
2021-03-02
2021-03-09
2021-03-11
2021-03-18
2021-03-23
2021-03-25
2021-03-30


In [ ]:
pip install jsonlines

In [ ]:
import jsonlines
with open("data.json", 'w') as f:
    for item in list_sen:
        f.write(json.dumps(item) + "\n")
with open("data.json") as f:
    for line in f:
        print(line)

流式输出内容被截断，只能显示最后 5000 行内容。
{"text": "When we offer the vaccine at those sites, most of the population who receive the vaccine will be the ones who actually live in the area.", "metadata": "02/08/2021-545"}

{"text": "Assembly Committee on Health and Human Services February 8, 2021 This issue is important to mention.", "metadata": "02/08/2021-546"}

{"text": "I was reading an article in The New York Times recently that mentioned health inequalities in this country.", "metadata": "02/08/2021-547"}

{"text": "An example was given of some large metropolitan areas deploying large vaccination sites mostly in affluent areas because it was easier to do that.", "metadata": "02/08/2021-548"}

{"text": "This is not the case in Clark County.", "metadata": "02/08/2021-549"}

{"text": "Our PODs are all within the areas where we have more cases; Cashman Center is just in the middle of all that action, as are all those schools where we have opened PODs.", "metadata": "02/08/2021-550"}

{"text": "Those

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



In [ ]:
import spacy

In [ ]:
query = 

In [ ]:
import openai

In [ ]:
openai.api_key = "YOUR-API-KEY"
response = openai.File.create(file=open("data.json"), purpose="search")
print(response)

AuthenticationError: ignored

In [ ]:
search_response = openai.Engine("davinci").search(
    search_model="davinci", 
    query="healthcare", 
    max_rerank=5,
    file="file-8ejPA5eM13J4J0dWy3bBbvTf",
    return_metadata=True
)

{datetime.date(2021, 2, 3): ['Chair Nguyen: [Roll was taken.]',
  'Good afternoon, everyone, and welcome to our first meeting of the Assembly Committee on Health and Human Services for the 81st Legislative Session.',
  'Thank you for joining us, and thank you to our virtual audience watching this online, on their phones, or on any other device available to them.',
  'Today we have some introductions, adoption of Committee policies, and a presentation by the staff of the Department of Health and Human Services.',
  'However, before we begin, I would like to make several housekeeping announcements.',
  'For those who do not know, the Assembly Committee on Health and Human Services is scheduled to meet Mondays, Wednesdays, and Fridays at 1:30 p.m.',
  'I will plan to start on time, so I have asked people to go online early, especially in this virtual setting, because we always have some difficulties.',
  'This is a virtual meeting format and meant to keep us safe during the COVID-19 pande